# Let's play ping pong

From one side, I will run this part including my GCN credentials as 'Producer', but streaming on the test version of GCN.

In [1]:
from gcn_kafka import Producer
import base64
import json

In [2]:
from credentials import load_credentials, get_credential, list_credentials

# Load credentials from credentials.txt
load_credentials()

# Check what's configured
print("Configured credentials:")
for key, status in list_credentials().items():
    print(f"  {key}: {status}")

# Access specific credentials when needed
try:
    gcn_client_id = get_credential('GCN_CLIENT_ID_PROD')
    gcn_client_secret = get_credential('GCN_CLIENT_SECRET_PROD')
    print(f"\n✅ GCN Client ID: {gcn_client_id[:10]}..." )
except ValueError as e:
    print(f"\n⚠️ {e}")

📖 Loading credentials from: /Users/samueleronchini/Desktop/acme_tutorials/alerts/credentials.txt
✅ Loaded 17 credentials
Configured credentials:
  GCN_CLIENT_ID: ✅ Configured
  GCN_CLIENT_SECRET: ✅ Configured
  FINK_USERNAME: ⚠️ Empty
  FINK_GROUP_ID: ⚠️ Empty
  FINK_SERVERS: ✅ Configured
  SLACK_WEBHOOK: ✅ Configured
  SLACK_CHANNEL_ID: ✅ Configured
  EMAIL_SENDER: ✅ Configured
  EMAIL_PASSWORD: ✅ Configured
  EMAIL_SMTP_SERVER: ✅ Configured
  EMAIL_SMTP_PORT: ✅ Configured
  EMAIL_RECIPIENT: ✅ Configured
  TELEGRAM_BOT_TOKEN: ✅ Configured
  GRACEDB_USERNAME: ⚠️ Empty
  GRACEDB_PASSWORD: ⚠️ Empty
  GCN_CLIENT_ID_PROD: ✅ Configured
  GCN_CLIENT_SECRET_PROD: ✅ Configured

✅ GCN Client ID: 1kkd46pj7a...


In [3]:
# Test
producer = Producer(config={'message.max.bytes': int(5 * 1024 * 1024)}, client_id= gcn_client_id, client_secret= gcn_client_secret, domain='test.gcn.nasa.gov')

In [11]:
with open('./guano.loc_map_758917906.json') as f:
    exnotice=json.load(f)

In [5]:
exnotice

{'$schema': 'https://gcn.nasa.gov/schema/v4.0.0/gcn/notices/swift/bat/guano.schema.json',
 'mission': 'Swift',
 'instrument': 'BAT-GUANO',
 'messenger': 'EM',
 'record_number': 1,
 'alert_datetime': 'none',
 'alert_tense': 'current',
 'alert_type': 'initial',
 'trigger_time': 'none',
 'healpix_file': '',
 'systematic_included': True,
 'rate_snr': None,
 'rate_duration': None,
 'rate_energy_range': [15, 350],
 'classification': {'GRB': 1},
 'far': None,
 'follow_up_event': 'none',
 'follow_up_type': 'GRB',
 'data_archive_page': 'none',
 'id': ['none']}

In [12]:
with open('./771151674_0_n_PROBMAP.fits', 'rb') as f:
    skymap_bytes = f.read()

In [13]:
enconded_map = base64.b64encode(skymap_bytes)

In [14]:
exnotice['healpix_file'] = enconded_map.decode()
example_str = json.dumps(exnotice)

In [15]:
len(example_str)/1024/1024  # size in MB

3.6296634674072266

In [16]:
producer.produce('gcn.notices.swift.bat.guano',example_str)
producer.flush()

0

On the other side, who will listen will have to set up the following. The credentials need to be created on https://test.gcn.nasa.gov/user/credentials

In [ ]:
from gcn_kafka import Consumer

consumer = Consumer(client_id='xxx',
                    client_secret='..',
                    domain='test.gcn.nasa.gov')

# Subscribe to topics and receive alerts
consumer.subscribe(['gcn.notices.swift.bat.guano'])
while True:
    for message in consumer.consume(timeout=1):
        if message.error():
            print(message.error())
            continue
        # Print the topic and message ID
        print(f'topic={message.topic()}, offset={message.offset()}')
        value = message.value()
        print(value)